# Prévision de précipitations de pluie en France métropolitaine (2016 - 2018)

Détails sur ce qui est attendu :
1. Explication du problème de machine learning que vous souhaitez résoudre
2. Présentation du jeu de données
3. Exploration du jeu de données (Analyse descriptive, statistiques descriptives, visualisation)
4. Data cleaning et imputation de données manquantes (si nécessaire)
5. Feature engineering en expliquant votre démarche et les variables créées
6. Préparation des données pour être fournies à un modèle de prévision ML/DL
7. Sélection de différents modèles (explications des critères de sélection, choix de la métrique,
…)

## Problématique

En début 2023, la crainte d'une sécheresse des nappes phréatiques en France souligne l'importance de prévoir précisément les précipitations. Les conséquences d'une mauvaise prédiction peuvent être graves, notamment des pénuries alimentaires, des inondations, une mauvaise gestion des ressources en eau et une propagation de maladies. Les prévisions météorologiques sont donc cruciales pour de nombreuses activités humaines, telles que l'agriculture, les transports et la gestion des ressources en eau.

Dans ce contexte, il est important de développer des modèles de prédiction précis pour améliorer la fiabilité des prévisions météorologiques. Pour ce projet de prévision, nous avons choisi de travailler à partir de données issues de Météo France, portant sur différents indicateurs mesurés sur une période d'étude de 2016-2018 et sur une majorité des stations météorologiques en France métropolitaine.

A ce stade, la problématique reste large et nous devons définir différents élements:
- Est-ce qu'on cherche à prédire de façon journalière, hebdomadaire, mensuelle, annuelle?
- Sur quel période on prédit? Sur toute une année? un mois? un jour?

Il s'agit de questions qui peuvent être répondues de différentes façons:
- métier: Prenons l'exemple des agriculteurs, la prévision la plus intéressante serait celle qui leur permettrait de planifier au mieux leurs cultures, de gérer efficacement les ressources en eau et de protéger leurs cultures contre les conditions climatiques extrêmes. En ce sens, une prévision à court-terme serait pertinente pour permettre de voir comment se protéger de conditions extrêmes (si une sécheresse est anticipée quelques jours/une semaine avant) mais également à long-terme pour organiser un plan de gestion de l'eau.
- les données: peut-être qu'il faut également voir la pertinence des prévisions à faire en fonction de la qualité des données: peut-être qu'il est plus facile de comprendre l'évolution future des précipitations en regardant sur l'ensemble du mois que sur un jour..






## Données
#### Description de la base de données: MeteoNet

MeteoNet, est un jeu de données proposé par Météo France dans le but de faciliter l'exploitation de données météorologiques par les Data Scientists. Ce jeu de données est accessible en ligne et contient des données d'archives de 3 ans, de 2016 à 2018, pour deux zones géographiques de 550 x 550 km sur le nord-ouest et le sud-est de la France. Il comprend:
- des images radar de précipitations
- des observations de 500 stations météorologiques
- des prévisions de modèles météorologiques 2D et 3D
- des masques terre/mer et relief

#### Description du jeu de données

Dans notre cas, nous nous intéresserons principalement aux observations des stations météorologiques. Voici une Overview de ce jeu de données à retrouver sur [MéteoNet](https://meteonet.umr-cnrm.fr/dataset/data/) (il faudra aller dans les répertoires NW/SE puis dans grounds_stations):
- NW2016
- NW2017
- NW2018
- SE2016
- SE2017
- SE2018

Il y a ainsi 6 sets de données qui contiennent comme l'indique leurs noms les données des stations météorologiques de 2016-2018 dans le Nord-Ouest et Sud-Est de la France. Chaque station météorologique recense différents indicateurs toutes les 6 minutes, concernant le vent,la pression, les précipitations, la température, etc...
Tout cela sera expliqué par la suite.

#### Création d'un jeu de données exploitable pour l'analyse 

##### Démarche

**Remarque**:
- Etant donné le volume conséquent de données (16Go, environ 195 millions de lignes en regroupant les 6 sets), nous vous proposons d'utiliser directement un jeu de données plus exploitable nommé 'data.csv' qui sera a récupérer dans le Drive. En plus, par défaut, le repo GitHub dispose d'un échantillon de 1000 observations pour la démo de cette partie ("data/sample/sample.csv")

- Nous tenions tout de même à expliquer les étapes réalisées pour obtenir ce jeu de données (qui sont réalisables si besoin depuis la base d'origine). Nous avons créé en plusieurs temps ce jeu de données. D'une part, nous avons appliqué les mêmes méthodes étapes Nord-Ouest puis Sud-Est (en traitant l'ensemble des csvs, le Kernel se bloquait):
    1) Concaténation des 3 csvs de 2016 à 2018
    3) Au vu de la proximité géographique des stations météorologiques, nous avons considéré qu'il serait pertinent de regrouper les stations de sorte à condenser l'information.


    
    4) Après avoir arrondi par heure la colonne des dates, nous allons ainsi aggréger par département les différents indicateurs en utilisant la moyenne:
        - D'abord, on aggrège par heure pour chaque station pour avoir la moyenne de chaque indicateur sur l'heure par station
        - Ensuite, on aggrège par département ces mêmes taux en utilisant la moyenne:  on aura typiquement pour chaque département, pour chaque jour, et chaque heure, le taux de précipitation moyen.

    Ensuite, nous avons simplement concaténé les deux dataframes pour obtenir "data.csv"



##### Exemple sur un échantillon de 1000 observations
Il était nécessaire de montrer les étapes nécessaires à la création du jeu de données de l'analyse. Ces étapes ont été réalisées à l'issu de différents choix, notamment pour les méthodes d'aggrégation.

In [2]:
##### Installation de l'environnement
import os
import importlib
import pandas as pd
import requests
import plotly.express as px
import json

os.chdir(os.path.dirname(os.getcwd()))

from scripts.extractor import get_h3_components,get_geojson_from_h3
from scripts.plots import plot_hexagons_on_mapbox


In [8]:
import dask.dataframe as dd
data = dd.read_csv(os.getcwd()+"/data/sample/*.csv", header=0)


In [16]:
data.head()

number_sta    lat   lon  height_sta       date     dd   ff  precip    hu  \
0    14066001  49.33 -0.43         2.0 2016-01-01  210.0  4.4     0.0  91.0   
1    14126001  49.15  0.04       125.0 2016-01-01    NaN  NaN     0.0  99.0   
2    14137001  49.18 -0.46        67.0 2016-01-01  220.0  0.6     0.0  92.0   
3    14216001  48.93 -0.15       155.0 2016-01-01  220.0  1.9     0.0  95.0   
4    14296001  48.80 -1.03       339.0 2016-01-01    NaN  NaN     0.0   NaN   

       td       t       psl  
0  278.45  279.85       NaN  
1  278.35  278.45       NaN  
2  276.45  277.65  102360.0  
3  278.25  278.95       NaN  
4     NaN  278.35       NaN

Les différentes colonnes sont:
- number_sta : identifiant unique de la station météorologique
- lat : latitude de la station
- lon : longitude de la station
- height_sta : hauteur de la station par rapport au niveau de la mer
- date : date et heure à laquelle les données ont été enregistrées (au format AAAAMMJJ HH:MM)
- dd : direction du vent (en degrés)
- ff : force du vent (en m/s)
- precip : quantité de précipitations (kg.m2)
- hu : humidité relative (en %)
- td : température du point de rosée (Kelvin (K))
- t : température (Kelvin (K))
- psl : pression au niveau de la mer (Pascal(Pa))


**Note**: Nous allons nous intéresser principalement à la pluie mais nous n'excluons pas d'utiliser les autres variables pour aider la prévision des précipitations.

On garde uniquement les stations observées sur les 3 années:

In [26]:
stations = data[["number_sta","lat","lon","height_sta","precip"]].drop_duplicates(subset="number_sta").compute()

In [27]:
stations

number_sta     lat    lon  height_sta  precip
0         14066001  49.330 -0.430         2.0     0.0
1         14126001  49.150  0.040       125.0     0.0
2         14137001  49.180 -0.460        67.0     0.0
3         14216001  48.930 -0.150       155.0     0.0
4         14296001  48.800 -1.030       339.0     0.0
...            ...     ...    ...         ...     ...
36046     20142001  41.700  9.124       622.0     0.0
668062    66024001  42.520  2.824        89.0     0.0
630575    11206003  43.046  2.201       230.0     0.0
50237     20272001  41.621  8.963       258.0     0.0
300813    13092001  43.550  5.037        10.0     0.0

[862 rows x 5 columns]

In [106]:
fig = px.scatter_mapbox(stations, lat="lat", lon="lon", zoom=3, color_discrete_sequence=['grey'])
fig.update_layout(mapbox_style="open-street-map")
fig.show()

Au vu du graphique précédent, on voit que les stations météorologiques sont nombreuses et certaines paraissent particulièrement proches les unes des autres. Il serait peut-être pertinent d'utiliser une méthode de segmentation géographique pour regrouper les stations. Dans un premier temps, nous avions envisagé une segmentation par département, mais cela peut englober des disparités entre les stations d'un même département (Pyrénées Atlantique).
De plus, si on laisse tel quel le jeu de données, le nombre d'observations est très élevé. Faisons ainsi une segmentation de type H3:

H3 est un système d'indexation géospatial hiérarchique hexagonal open-source développé par Uber. Il s'agit d'un système permettant de partitionner la surface de la Terre en cellules hexagonales de tailles différentes pouvant être utilisées pour l'indexation et la recherche spatiale. 

La taille des cellules hexagonales peut varier: on peut décider une maille très fine (moins d' 1km2 par cellule) tout comme d'une maille assez large pour englober un pays par exemple.

On choisit la taille de la maille adaptée graphiquement: on cherche un compromis entre le nombre de groupes formé et le nombre de stations par groupe. En ce sens une maille de taille 3 semble pertinente au vu du graphique suivant:


In [107]:
hex_size=4
get_h3_components(stations,hex_size=hex_size)
plot_hexagons_on_mapbox(stations, color='red')

print(f"""Nombre de groupes avec une maille de {hex_size}: {stations["h3_hex_id"].nunique()}""")

Nombre de groupes avec une maille de 4: 218


In [105]:
hex_size=3
get_h3_components(stations,hex_size=hex_size)
plot_hexagons_on_mapbox(stations, color='red')

print(f"""Nombre de groupes avec une maille de {hex_size}: {stations["h3_hex_id"].nunique()}""")

Nombre de groupes avec une maille de 3: 46


In [ ]:
json_hex_ids=get_geojson_from_h3(stations)
with open('data/extras/h3.json', 'w') as outfile:
    json.dump(json_hex_ids, outfile)

Aggrégations:
1)  On arrondit par heure (à l'heure la plus près) et on récupère la moyenne pour chaque station et heure de chaque indicateur. Remarque: La moyenne nous a paru la façon d'aggréger la plus pertinente (La somme aurait causé des inégalités entre les stations qui sont observés plusieurs fois dans une même heure et celles qui le sont moins/La médiane ne reflétait pas nécessairement les outliers, qui doivent ressortir dans le contexte des indicateurs météorologiques)
2) On merge avec le dataframe des stations (pour lequel on a récupéré les départements)
3) On fait ensuite l'aggrégation par département et par heure en faisant également la moyenne de chaque indicateur (pour les mêmes raisons que l'aggrégation par station)

In [33]:
indicators = ["dd","ff","precip","hu","td","t","psl"]
aggregator = "h3_hex_id"

# 1) Regrouper les données par station et date, puis calculer la moyenne des indicateurs
data = data.groupby(["number_sta", "date"])[indicators].mean().reset_index()

# Convertir la colonne 'date' en datetime et arrondir à l'heure
data['date'] = dd.to_datetime(data['date'], format="%Y%m%d %H:%M").dt.round("H")

# 2) Joindre les données avec les informations de l'aggrégateur
data_with_hex = dd.merge(data, stations[["number_sta", aggregator]], how="left", on="number_sta")

# 3) Regrouper les données par agrégateur et date, puis calculer la moyenne des indicateurs
data_with_hex = data_with_hex.groupby([aggregator, "date"])[indicators].mean().reset_index()


In [34]:
data_with_hex.head(10)

h3_hex_id                date          dd         ff    precip  \
0  831840fffffffff 2016-01-01 00:00:00  140.000000   1.783333  0.000000   
1  831840fffffffff 2016-01-01 01:00:00  147.777778   3.122222  0.000000   
2  831840fffffffff 2016-01-01 02:00:00  147.272727   4.581818  0.000000   
3  831840fffffffff 2016-01-01 03:00:00  138.888889   5.955556  0.000000   
4  831840fffffffff 2016-01-01 04:00:00  158.181818   6.163636  0.036364   
5  831840fffffffff 2016-01-01 05:00:00  170.000000   6.066667  0.000000   
6  831840fffffffff 2016-01-01 06:00:00  153.636364   6.200000  0.000000   
7  831840fffffffff 2016-01-01 07:00:00  165.555556   8.133333  0.000000   
8  831840fffffffff 2016-01-01 08:00:00  160.000000  10.918182  0.054545   
9  831840fffffffff 2016-01-01 09:00:00  150.000000  14.044444  0.000000   

          hu          td           t            psl  
0  85.333333  281.300000  283.633333  102240.000000  
1  80.666667  281.072222  284.283333  102212.222222  
2  78.272727  280.904545  284.550000  102146.363636  
3  81.555556  281.872222  284.938889  102094.444444  
4  84.727273  282.195455  284.695455  102030.909091  
5  83.111111  282.083333  284.861111  101941.111111  
6  85.000000  282.686364  285.131818  101847.272727  
7  80.000000  282.305556  285.661111  101766.666667  
8  79.454545  282.068182  285.522727  101663.636364  
9  78.000000  281.861111  285.572222  101588.888889

In [40]:
data_with_hex=data_with_hex.compute()

In [42]:
data_with_hex.to_csv("data/intermediate/data.csv")

## Exploration des données

##### Importation des données
Pour notre analyse, nous avons besoin du dataframe "data.csv" disponible dans "data/intermediate" et de "departements.geojson" disponible dans "data/extras" (Récupéré via le [lien](https://github.com/gregoiredavid/france-geojson/blob/master/departements.geojson))

In [50]:
import json

data = pd.read_csv("data/intermediate/data.csv")
data.drop(columns="Unnamed: 0",inplace=True) 
data['date'] = pd.to_datetime(data['date'], format='%Y%m%d %H:%M')

In [51]:
data.shape

(1208444, 9)

In [93]:
data["day_date"]=data["date"].round("D")
data["month_date"]=data["date"].dt.strftime('%Y-%m')
data["year_date"]=data["date"].dt.strftime('%Y')
data["week_date"] = data["date"].dt.week


In [95]:
data_2016 = data[data["date"].dt.year ==2016]

data_2016_by_day = data_2016.groupby(["h3_hex_id","day_date"])[indicators].median().reset_index()
data_2016_by_month = data_2016.groupby(["h3_hex_id","month_date"])[indicators].median().reset_index()
data_2016_by_year = data_2016.groupby(["h3_hex_id","year_date"])[indicators].median().reset_index()
data_2016_by_week = data_2016.groupby(["h3_hex_id","week_date"])[indicators].median().reset_index()

In [96]:
data_by_day = data.groupby(["h3_hex_id","day_date"])[indicators].mean().reset_index()
data_by_month = data.groupby(["h3_hex_id","month_date"])[indicators].mean().reset_index()
data_by_year = data.groupby(["h3_hex_id","year_date"])[indicators].mean().reset_index()
data_by_week = data.groupby(["h3_hex_id","week_date"])[indicators].mean().reset_index()



#### Focus sur une année

In [99]:
import plotly.express as px
fig = px.line(data_2016_by_day, x='day_date', y="precip",color="h3_hex_id")
fig.show()

In [100]:
import plotly.express as px
fig = px.line(data_2016_by_week, x='week_date', y="precip",color="h3_hex_id")
fig.show()

In [101]:
import plotly.express as px
fig = px.line(data_2016_by_month, x='month_date', y="precip",color="h3_hex_id")
fig.show()

#### Overview

In [97]:
import plotly.express as px
fig = px.line(data_by_day, x='day_date', y="precip",color="h3_hex_id")
fig.show()

In [104]:
import plotly.express as px
fig = px.line(data_by_week, x='week_date', y="precip",color="h3_hex_id")
fig.show()

In [103]:
import plotly.express as px
fig = px.line(data_by_month, x='month_date', y="precip",color="h3_hex_id")
fig.show()

In [92]:
import plotly.express as px
fig = px.line(data_by_year, x='year_date', y="precip",color="h3_hex_id")
fig.show()


Interprétation:
Que ce soit niveau annuel, mensuel, ...